In [4]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!pip install geopy
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Visualization modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [5]:
with open('new_york_data.json') as json_data:
    newyork_data = json.load(json_data)

In [6]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

The data we need from this json data file is 
 1. Borough Name
 2. Neighbourhood
 3. Latitude
 4. Longitude
 
we will make a pandas dataframe with the 4 columns as listed above but before making the dataframe we will extract what we need.

In [7]:
newyork_df = pd.DataFrame(columns = ['Borough_name','Neighborhood','Latitude','Longitude'])
newyork_df

Empty DataFrame
Columns: [Borough_name, Neighborhood, Latitude, Longitude]
Index: []

In [8]:
newyork_data_clean = newyork_data['features']
for data in newyork_data_clean:
    
    neighborhood = data['properties']['name']
    borough = data['properties']['borough']
    location = data['geometry']['coordinates']
    longitude,latitude = location[0],location[1]
    data = {"Borough_name":borough,"Neighborhood":neighborhood,"Latitude":latitude,"Longitude":longitude}
    newyork_df = newyork_df.append(data,ignore_index=True)
    
    

In [9]:
newyork_df.head()

Borough_name Neighborhood   Latitude  Longitude
0        Bronx    Wakefield  40.894705 -73.847201
1        Bronx   Co-op City  40.874294 -73.829939
2        Bronx  Eastchester  40.887556 -73.827806
3        Bronx    Fieldston  40.895437 -73.905643
4        Bronx    Riverdale  40.890834 -73.912585

In [10]:
newyork_df['Borough_name'].value_counts()

Queens           81
Brooklyn         70
Staten Island    63
Bronx            52
Manhattan        40
Name: Borough_name, dtype: int64

In [11]:
newyork_df.shape

(306, 4)

The dataframe consists of Five Boroughs and 306 Neighborhoods. 

Use geopy library to get the latitude and longitude values of New York City.

In [12]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


# Create a map of New York with neighborhoods superimposed on top.

In [13]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(newyork_df['Latitude'], newyork_df['Longitude'], newyork_df['Borough_name'], newyork_df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

# Create map of Manhattan Borough.

In [14]:
manhattan_data = newyork_df[newyork_df['Borough_name'] == 'Manhattan'].reset_index(drop=True)

Let's get the geographical coordinates of Manhattan.

In [15]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7900869, -73.9598295.


In [16]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

# Let's explore the first neighborhood in Manhattan Borough.

In [17]:
manhattan_data.loc[0, 'Neighborhood']

'Marble Hill'

Get the neighborhood's latitude and longitude values.

In [18]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = manhattan_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Marble Hill are 40.87655077879964, -73.91065965862981.


Now, let's get the top 100 venues that are in Marble Hill within a radius of 1000 meters.

Define Foursquare Credentials and Version.

In [69]:
CLIENT_ID = 'I4D4A1JPPOZV3TKA0ZQ12JORYAAAMWRIK5D5K1THXH5LECKU' # your Foursquare ID
CLIENT_SECRET = '2MWZDT2HP0NODCSYOQHM3YDBMTJI3SUGGT3XE5GPHINMCZRC' # your Foursquare Secret
VERSION = '20190604'

In [20]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 1000 # define radius
# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=BI0VHR1QJSEIBDYHKBMBWWXCXNBTFZOCHFWQRQVSEYZYP3CY&client_secret=3RL3VDQV254P0IXMDNB3ARNFYIMIUQ21PQMPEK5D1JFHJBVD&v=20190604&ll=40.87655077879964,-73.91065965862981&radius=1000&limit=100'

In [21]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5d7fc6b86001bc00384df5e6'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 82,
  'suggestedBounds': {'ne': {'lat': 40.88555078779965,
    'lng': -73.89877901972629},
   'sw': {'lat': 40.86755076979963, 'lng': -73.92254029753333}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4baf59e8f964a520a6f93be3',
       'name': 'Bikram Yoga',
       'location': {'address': '5500 Broadway',
        'crossStreet': '230th Street',
        'lat': 40.876843690797934,
        'lng': -73.9062038

In [22]:
manhattan_venues = pd.DataFrame(columns = ["Venue", "Latitude","Longitude","Address","Category"])
manhattan_venues

Empty DataFrame
Columns: [Venue, Latitude, Longitude, Address, Category]
Index: []

In [23]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

In [24]:
nearby_venues.head()

reasons.count                                      reasons.items  \
0              0  [{'summary': 'This spot is popular', 'type': '...   
1              0  [{'summary': 'This spot is popular', 'type': '...   
2              0  [{'summary': 'This spot is popular', 'type': '...   
3              0  [{'summary': 'This spot is popular', 'type': '...   
4              0  [{'summary': 'This spot is popular', 'type': '...   

                       referralId  \
0  e-0-4baf59e8f964a520a6f93be3-0   
1  e-0-4b4429abf964a52037f225e3-1   
2  e-0-4b79cc46f964a520c5122fe3-2   
3  e-0-4bb114c4f964a520b9783ce3-3   
4  e-0-55f81cd2498ee903149fcc64-4   

                                    venue.categories venue.delivery.id  \
0  [{'id': '4bf58dd8d48988d102941735', 'name': 'Y...               NaN   
1  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...             72548   
2  [{'id': '4bf58dd8d48988d147941735', 'name': 'D...               NaN   
3  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...               NaN   
4  [{'id': '4bf58dd8d48988d1e0931735', 'name': 'C...               NaN   

          venue.delivery.provider.icon.name  \
0                                       NaN   
1  /delivery_provider_seamless_20180129.png   
2                                       NaN   
3                                       NaN   
4                                       NaN   

        venue.delivery.provider.icon.prefix  \
0                                       NaN   
1  https://fastly.4sqi.net/img/general/cap/   
2                                       NaN   
3                                       NaN   
4                                       NaN   

  venue.delivery.provider.icon.sizes venue.delivery.provider.name  \
0                                NaN                          NaN   
1                           [40, 50]                     seamless   
2                                NaN                          NaN   
3                                NaN                          NaN   
4                                NaN                          NaN   

                                  venue.delivery.url  \
0                                                NaN   
1  https://www.seamless.com/menu/arturos-pizza-51...   
2                                                NaN   
3                                                NaN   
4                                                NaN   

                   venue.id venue.location.address venue.location.cc  \
0  4baf59e8f964a520a6f93be3          5500 Broadway                US   
1  4b4429abf964a52037f225e3          5198 Broadway                US   
2  4b79cc46f964a520c5122fe3       3033 Tibbett Ave                US   
3  4bb114c4f964a520b9783ce3         232 W 231st St                US   
4  55f81cd2498ee903149fcc64         171 W 230th St                US   

  venue.location.city venue.location.country venue.location.crossStreet  \
0               Bronx          United States               230th Street   
1            New York          United States               at 225th St.   
2               Bronx          United States         btwn 230th & 231st   
3               Bronx          United States             Godwin Terrace   
4               Bronx          United States                Kimberly Pl   

   venue.location.distance                    venue.location.formattedAddress  \
0                      376  [5500 Broadway (230th Street), Bronx, NY 10463...   
1                      240  [5198 Broadway (at 225th St.), New York, NY 10...   
2                      452  [3033 Tibbett Ave (btwn 230th & 231st), Bronx,...   
3                      516  [232 W 231st St (Godwin Terrace), Bronx, NY 10...   
4                      441  [171 W 230th St (Kimberly Pl), Bronx, NY 10463...   

                       venue.location.labeledLatLngs  venue.location.lat  \
0  [{'label': 'display', 'lat': 40.87684369079793...           40.876844   
1  [{'label': 'display', 'lat': 40.87441177110231...           40.8

In [25]:
venues

[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4baf59e8f964a520a6f93be3',
   'name': 'Bikram Yoga',
   'location': {'address': '5500 Broadway',
    'crossStreet': '230th Street',
    'lat': 40.876843690797934,
    'lng': -73.90620384419528,
    'labeledLatLngs': [{'label': 'display',
      'lat': 40.876843690797934,
      'lng': -73.90620384419528}],
    'distance': 376,
    'postalCode': '10463',
    'cc': 'US',
    'city': 'Bronx',
    'state': 'NY',
    'country': 'United States',
    'formattedAddress': ['5500 Broadway (230th Street)',
     'Bronx, NY 10463',
     'United States']},
   'categories': [{'id': '4bf58dd8d48988d102941735',
     'name': 'Yoga Studio',
     'pluralName': 'Yoga Studios',
     'shortName': 'Yoga Studio',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/gym_yogastudio_',
      'suffix': '.png'},
     'primary': True}],


We have our information in 'Venue.name' ,'venue.categories', 'venue.location.lat', 'venue.location.lng', "venue.location.formattedAddress". We have to a function to Venue.categories to extract the Venue Category.

In [26]:
# function that extracts the category of the venue
def get_category_type(row):
    
    categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [27]:
# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

In [28]:
nearby_venues.head()

venue.name venue.categories  venue.location.lat  venue.location.lng
0    Bikram Yoga      Yoga Studio           40.876844          -73.906204
1       Arturo's      Pizza Place           40.874412          -73.910271
2  Tibbett Diner            Diner           40.880404          -73.908937
3    Sam's Pizza      Pizza Place           40.879435          -73.905859
4      Starbucks      Coffee Shop           40.877531          -73.905582

In [29]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

82 venues were returned by Foursquare.


# Similarly let's extract venues for all the neighbourhoods in Newyork City.

Let's create a function to repeat the same process to all the neighborhoods in each Borough.

In [36]:
def getNearbyVenues(borough,names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()
        #print(results)
        results = results["response"]["groups"][0]["items"]
        
        # return only relevant information for each nearby venue
            
        venues_list.append([(
            borough,
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']
            ) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    
    nearby_venues.columns = ['Borough','Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

In [31]:
boroughs = newyork_df['Borough_name'].unique().tolist()

In [32]:
boroughs

['Bronx', 'Manhattan', 'Brooklyn', 'Queens', 'Staten Island']

In [38]:
Master_df = pd.DataFrame(columns = ['Borough','Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category'])
borough = boroughs[0]
print('Finding Venues around {} '.format(borough))
borough_data = newyork_df[newyork_df['Borough_name'] == borough].reset_index(drop=True)
    #print(borough_data.head())
borough_venues = getNearbyVenues(borough,names=borough_data['Neighborhood'],
                                   latitudes=borough_data['Latitude'],
                                   longitudes=borough_data['Longitude']
                                  )
Master_df = Master_df.append(borough_venues,ignore_index = True)
    
print('Concatenated {}_venues dataframe to Master dataframe'.format(borough))
print("....................................................................")

Finding Venues around Bronx 


KeyError: 'groups'

In [34]:
borough = boroughs[1]
print('Finding Venues around {} '.format(borough))
borough_data = newyork_df[newyork_df['Borough_name'] == borough].reset_index(drop=True)
    #print(borough_data.head())
borough_venues = getNearbyVenues(borough,names=borough_data['Neighborhood'],
                                   latitudes=borough_data['Latitude'],
                                   longitudes=borough_data['Longitude']
                                  )
Master_df = Master_df.append(borough_venues,ignore_index = True)
    
print('Concatenated {}_venues dataframe to Master dataframe'.format(borough))
print("....................................................................")

Finding Venues around Manhattan 
{'meta': {'code': 200, 'requestId': '5d7fc6dab77c77002c0381f6'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Marble Hill', 'headerFullLocation': 'Marble Hill, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 24, 'suggestedBounds': {'ne': {'lat': 40.88105078329964, 'lng': -73.90471933917806}, 'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b4429abf964a52037f225e3', 'name': "Arturo's", 'location': {'address': '5198 Broadway', 'crossStreet': 'at 225th St.', 'lat': 40.87441177110231, 'lng': -73.91027100981574, 'labeledLatLngs': [{'label': 'display', 'lat': 40.87441177110231, 'lng': -73.91027100981574}], 'distan

{'meta': {'code': 200, 'requestId': '5d7fc6da598e64002cfecb63'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Chinatown', 'headerFullLocation': 'Chinatown, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 235, 'suggestedBounds': {'ne': {'lat': 40.720118426814324, 'lng': -73.98835342594391}, 'sw': {'lat': 40.71111841781432, 'lng': -74.00020529917565}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '578692f4498e1054905dbde7', 'name': 'Hotel 50 Bowery NYC', 'location': {'address': '50 Bowery', 'crossStreet': 'btwn Bayard & Canal St', 'lat': 40.7159364, 'lng': -73.9967894, 'labeledLatLngs': [{'label': 'display', 'lat': 40.7159364, 'lng': -73.9967894}], 'distance': 214, 

{'meta': {'code': 200, 'requestId': '5d7fc6dbc53093003725f7c8'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Hudson Heights', 'headerFullLocation': 'Hudson Heights, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 86, 'suggestedBounds': {'ne': {'lat': 40.85640253005305, 'lng': -73.93096217082847}, 'sw': {'lat': 40.84740252105305, 'lng': -73.94283838887621}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5547b2fb498e5a61fb5c80de', 'name': 'Green Juice Cafe', 'location': {'lat': 40.85189793238417, 'lng': -73.93482699423339, 'labeledLatLngs': [{'label': 'display', 'lat': 40.85189793238417, 'lng': -73.93482699423339}], 'distance': 174, 'postalCode': '10033', 'cc': 'US

{'meta': {'code': 200, 'requestId': '5d7fc6dc6f0aa20039366fe4'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': '$-$$$$', 'key': 'price'}, {'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Inwood', 'headerFullLocation': 'Inwood, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 57, 'suggestedBounds': {'ne': {'lat': 40.87218396899915, 'lng': -73.91527089806932}, 'sw': {'lat': 40.86318395999915, 'lng': -73.92714994600861}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4ad9ef84f964a520111c21e3', 'name': 'PJ Wine', 'location': {'address': '4898 Broadway', 'crossStreet': '204', 'lat': 40.86725069863996, 'lng': -73.92234862213004, 'labeledLatLngs': [{'label': 'display', 'lat': 40.86725069863996, 'lng': -73.92234862213004}], 'distance': 107, 'postal

{'meta': {'code': 200, 'requestId': '5d7fc6dd86bc49002c2394aa'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'West Harlem', 'headerFullLocation': 'West Harlem, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 61, 'suggestedBounds': {'ne': {'lat': 40.82810428931194, 'lng': -73.94375234418293}, 'sw': {'lat': 40.81910428031193, 'lng': -73.9556234934844}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '51b15855498e85fb32404731', 'name': 'The Grange Bar & Eatery', 'location': {'address': '1635 Amsterdam Ave', 'crossStreet': '141st St', 'lat': 40.822553515536654, 'lng': -73.9495322849762, 'labeledLatLngs': [{'label': 'display', 'lat': 40.822553515536654, 'lng': -73.949532

...

{'meta': {'code': 200, 'requestId': '5d7fc6ed6f0aa2003936c956'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': '$-$$$$', 'key': 'price'}, {'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Lower East Side', 'headerFullLocation': 'Lower East Side, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 61, 'suggestedBounds': {'ne': {'lat': 40.72230675342765, 'lng': -73.97496418858248}, 'sw': {'lat': 40.71330674442765, 'lng': -73.98681645140334}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '57e6eb33498e2033ea2cf36f', 'name': 'Spoke Art NYC', 'location': {'address': '210 Rivington St', 'lat': 40.71839474548904, 'lng': -73.98284352723249, 'labeledLatLngs': [{'label': 'display', 'lat': 40.71839474548904, 'lng': -73.98284352723249}], 'distance': 177, 'p

{'meta': {'code': 200, 'requestId': '5d7fc6ee86bc49002c23f617'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Tribeca', 'headerFullLocation': 'Tribeca, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 117, 'suggestedBounds': {'ne': {'lat': 40.72602197194322, 'lng': -74.00475682341998}, 'sw': {'lat': 40.717021962943214, 'lng': -74.01660974776176}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4ba0e528f964a5205c8537e3', 'name': 'Pier 26 - Hudson River Park', 'location': {'address': 'West St', 'crossStreet': 'at Beach St', 'lat': 40.72094711352765, 'lng': -74.0129479765892, 'labeledLatLngs': [{'label': 'display', 'lat': 40.72094711352765, 'lng': -74.0129479765892}], 

{'meta': {'code': 200, 'requestId': '5d7fc6ef49cf9300389c6366'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Little Italy', 'headerFullLocation': 'Little Italy, New York', 'headerLocationGranularity': 'neighborhood', 'totalResults': 234, 'suggestedBounds': {'ne': {'lat': 40.72382379845907, 'lng': -73.99137840561747}, 'sw': {'lat': 40.71482378945907, 'lng': -74.003230938544}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53506fd9498ebca706a7c170', 'name': 'La Compagnie des Vins Surnaturels', 'location': {'address': '249 Centre St', 'crossStreet': 'at Broome St', 'lat': 40.720447943059405, 'lng': -73.9979693380989, 'labeledLatLngs': [{'label': 'display', 'lat': 40.720447943059405, 'lng':

{'meta': {'code': 429, 'errorType': 'quota_exceeded', 'errorDetail': 'Quota exceeded', 'requestId': '5d7fc6ef6adbf5002c8ce6cc'}, 'response': {}}


KeyError: 'groups'

In [ ]:
borough = boroughs[2]
print('Finding Venues around {} '.format(borough))
borough_data = newyork_df[newyork_df['Borough_name'] == borough].reset_index(drop=True)
    #print(borough_data.head())
borough_venues = getNearbyVenues(borough,names=borough_data['Neighborhood'],
                                   latitudes=borough_data['Latitude'],
                                   longitudes=borough_data['Longitude']
                                  )
Master_df = Master_df.append(borough_venues,ignore_index = True)
    
print('Concatenated {}_venues dataframe to Master dataframe'.format(borough))
print("....................................................................")

In [ ]:
borough = boroughs[3]
print('Finding Venues around {} '.format(borough))
borough_data = newyork_df[newyork_df['Borough_name'] == borough].reset_index(drop=True)
    #print(borough_data.head())
borough_venues = getNearbyVenues(borough,names=borough_data['Neighborhood'],
                                   latitudes=borough_data['Latitude'],
                                   longitudes=borough_data['Longitude']
                                  )
Master_df = Master_df.append(borough_venues,ignore_index = True)
    
print('Concatenated {}_venues dataframe to Master dataframe'.format(borough))
print("....................................................................")

In [ ]:
borough = boroughs[4]
print('Finding Venues around {} '.format(borough))
borough_data = newyork_df[newyork_df['Borough_name'] == borough].reset_index(drop=True)
    #print(borough_data.head())
borough_venues = getNearbyVenues(borough,names=borough_data['Neighborhood'],
                                   latitudes=borough_data['Latitude'],
                                   longitudes=borough_data['Longitude']
                                  )
Master_df = Master_df.append(borough_venues,ignore_index = True)
    
print('Concatenated {}_venues dataframe to Master dataframe'.format(borough))
print("....................................................................")



Master_df consists of all neighbourboods with nearest venues,It's Name,locations and Category.

In [ ]:
Master_df.to_csv("Master.csv")

In [43]:
Master_df = pd.read_csv("Master.csv")

In [44]:
Master_df.head()

Unnamed: 0 Borough Neighborhood  Neighborhood Latitude  \
0           0   Bronx    Wakefield              40.894705   
1           1   Bronx    Wakefield              40.894705   
2           2   Bronx    Wakefield              40.894705   
3           3   Bronx    Wakefield              40.894705   
4           4   Bronx    Wakefield              40.894705   

   Neighborhood Longitude                                    Venue  \
0              -73.847201                         Lollipops Gelato   
1              -73.847201                                 Rite Aid   
2              -73.847201                         Carvel Ice Cream   
3              -73.847201  Cooler Runnings Jamaican Restaurant Inc   
4              -73.847201                                    Shell   

   Venue Latitude  Venue Longitude        Venue Category  
0       40.894123       -73.845892          Dessert Shop  
1       40.896649       -73.844846              Pharmacy  
2       40.890487       -73.848568        Ice Cream Shop  
3       40.898276       -73.850381  Caribbean Restaurant  
4       40.894187       -73.845862           Gas Station

In [48]:
Master_df.columns

Index(['Unnamed: 0', 'Borough', 'Neighborhood', 'Neighborhood Latitude',
       'Neighborhood Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude',
       'Venue Category'],
      dtype='object')

In [49]:
Master_df.drop(columns = 'Unnamed: 0',inplace = True,axis = 1)

In [50]:
Master_df.head()

Borough Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   Bronx    Wakefield              40.894705              -73.847201   
1   Bronx    Wakefield              40.894705              -73.847201   
2   Bronx    Wakefield              40.894705              -73.847201   
3   Bronx    Wakefield              40.894705              -73.847201   
4   Bronx    Wakefield              40.894705              -73.847201   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato       40.894123       -73.845892   
1                                 Rite Aid       40.896649       -73.844846   
2                         Carvel Ice Cream       40.890487       -73.848568   
3  Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
4                                    Shell       40.894187       -73.845862   

         Venue Category  
0          Dessert Shop  
1              Pharmacy  
2        Ice Cream Shop  
3  Caribbean Restaurant  
4           Gas Station

# Suppose you want to start a Car Rental Business let's see which areas are suitable.

In [52]:
car_df = Master_df[Master_df['Venue Category'].str.contains('[Cc]ar')]

In [53]:
car_df.head()

Borough Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
3    Bronx    Wakefield              40.894705              -73.847201   
26   Bronx  Eastchester              40.887556              -73.827806   
32   Bronx  Eastchester              40.887556              -73.827806   
36   Bronx  Eastchester              40.887556              -73.827806   
64   Bronx  Kingsbridge              40.881687              -73.902818   

                                      Venue  Venue Latitude  Venue Longitude  \
3   Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
26                              Fish & Ting       40.885539       -73.829151   
32        Golden Krust Caribbean Restaurant       40.888543       -73.831278   
36                   Royal Caribbean Bakery       40.888252       -73.831457   
64                               El Malecon       40.879338       -73.904457   

          Venue Category  
3   Caribbean Restaurant  
26  Caribbean Restaurant  
32  Caribbean Restaurant  
36  Caribbean Restaurant  
64  Caribbean Restaurant

In [54]:
car_df['Venue Category'].unique()

array(['Caribbean Restaurant', 'Rental Car Location', 'Daycare',
       'Child Care Service'], dtype=object)

In [55]:
rental_car = car_df[car_df['Venue Category'] == 'Rental Car Location']

In [56]:
rental_car.head()

Borough    Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
91     Bronx     Kingsbridge              40.881687              -73.902818   
137    Bronx        Woodlawn              40.898273              -73.867315   
515    Bronx         Melrose              40.819754              -73.909422   
826    Bronx         Belmont              40.857277              -73.888452   
1011   Bronx  Pelham Gardens              40.862966              -73.841612   

                                    Venue  Venue Latitude  Venue Longitude  \
91                  Enterprise Rent-A-Car       40.879866       -73.903847   
137                 Enterprise Rent-A-Car       40.896091       -73.865364   
515   Zipcar 155 St & 3 Ave - Bronx (MPG)       40.818924       -73.914068   
826                 Enterprise Rent-A-Car       40.858491       -73.884325   
1011                  Budget Truck Rental       40.865890       -73.837101   

           Venue Category  
91    Rental Car Location  
137   Rental Car Location  
515   Rental Car Location  
826   Rental Car Location  
1011  Rental Car Location

Let's Visualize them on a heat map.

In [63]:
from folium import plugins
m = folium.Map([40.7127281, -74.0060152], zoom_start=11)
# mark each station as a point
for index, row in rental_car.iterrows():
    folium.CircleMarker([row['Venue Latitude'], row['Venue Longitude']],
                        radius=2,
                        popup=row['Venue'],
                        fill_color="#3db7e4", # divvy color
                       ).add_to(m)
# convert to (n, 2) nd-array format for heatmap
CarArr = rental_car[['Venue Latitude', 'Venue Longitude']].as_matrix()

# plot heatmap
m.add_children(plugins.HeatMap(CarArr, radius=15))
m

C:\Users\Welcome\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  # This is added back by InteractiveShellApp.init_path()
C:\Users\Welcome\Anaconda3\lib\site-packages\ipykernel_launcher.py:14: FutureWarning: Method `add_children` is deprecated. Please use `add_child` instead.
  


Let's figure out which Neighbourhoods has these businesses and then suggest a neighbourhood for opening a Car Rental Business.

The number of rental car businesses are 22 in entire Newyork city and Neighbourhood Stein way has the highest number of rental car shops.

Let's superimpose neighbourhoods on top of heat map.

In [67]:
for index, row in rental_car.iterrows():
    folium.Marker([row['Neighborhood Latitude'], row['Neighborhood Longitude']],
                        radius=2,
                        popup=row['Neighborhood'],
                       ).add_to(m)
m

Let's explore venues around these neighborhoods and see if we can get some insights.

In [70]:
borough_data = rental_car
    #print(borough_data.head())
car_rental_venues = getNearbyVenues(borough,names=borough_data['Neighborhood'],
                                   latitudes=borough_data['Neighborhood Latitude'],
                                   longitudes=borough_data['Neighborhood Longitude']
                                  )

    
print("Found all Venues in those neighborhoods where there are car rental businesses.")
print("....................................................................")

{'meta': {'code': 200, 'requestId': '5d7ff54bf1110b002be97d8d'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Kingsbridge', 'headerFullLocation': 'Kingsbridge, Bronx', 'headerLocationGranularity': 'neighborhood', 'totalResults': 69, 'suggestedBounds': {'ne': {'lat': 40.88618737570521, 'lng': -73.89687720680473}, 'sw': {'lat': 40.87718736670521, 'lng': -73.90875876768737}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4af8b2c0f964a520460f22e3', 'name': 'Garden Gourmet Market', 'location': {'address': '5665 Broadway', 'crossStreet': 'btwn W 233rd & W 234th St', 'lat': 40.88135023917183, 'lng': -73.90338943716417, 'labeledLatLngs': [{'label': 'display', 'lat': 40.88135023917183, 'lng': -73

{'meta': {'code': 200, 'requestId': '5d7ff54c92e7a9002c37fbb1'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Woodlawn Heights', 'headerFullLocation': 'Woodlawn Heights, Bronx', 'headerLocationGranularity': 'neighborhood', 'totalResults': 29, 'suggestedBounds': {'ne': {'lat': 40.902772616638046, 'lng': -73.86137269842366}, 'sw': {'lat': 40.89377260763804, 'lng': -73.87325723785987}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4ba50da6f964a52046d638e3', 'name': 'Katonah Pizza and Pasta', 'location': {'address': '4307 Katonah Ave', 'lat': 40.89878411126604, 'lng': -73.86745706580207, 'labeledLatLngs': [{'label': 'display', 'lat': 40.89878411126604, 'lng': -73.86745706580207}], 'distance

{'meta': {'code': 200, 'requestId': '5d7ff54da30619002c800ea5'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'West Bronx', 'headerFullLocation': 'West Bronx, Bronx', 'headerLocationGranularity': 'neighborhood', 'totalResults': 27, 'suggestedBounds': {'ne': {'lat': 40.82425437509494, 'lng': -73.90348637744054}, 'sw': {'lat': 40.81525436609493, 'lng': -73.91535683770817}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4f0f4fe14fc6e3adf353a950', 'name': 'Blink Fitness', 'location': {'address': '744 Saint Anns Ave', 'crossStreet': "St. Ann's Avenue & E 156 St", 'lat': 40.81954303461479, 'lng': -73.91055416353106, 'labeledLatLngs': [{'label': 'display', 'lat': 40.81954303461479, 'lng': -73.91055416353106}], 'distance': 98, 'pos

{'meta': {'code': 200, 'requestId': '5d7ff54d6e46500039816b20'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Belmont', 'headerFullLocation': 'Belmont, Bronx', 'headerLocationGranularity': 'neighborhood', 'totalResults': 101, 'suggestedBounds': {'ne': {'lat': 40.86177710523896, 'lng': -73.88251337057221}, 'sw': {'lat': 40.85277709623895, 'lng': -73.8943905521239}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4acf80aef964a52025d420e3', 'name': "Tino's Delicatessen", 'location': {'address': '2410 Arthur Ave', 'crossStreet': 'E. 187 St.', 'lat': 40.85588217093613, 'lng': -73.88716612015719, 'labeledLatLngs': [{'label': 'display', 'lat': 40.85588217093613, 'lng': -73.88716612015719}], 'dis

{'meta': {'code': 200, 'requestId': '5d7ff54ed69ed00039ed38b1'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}, {'name': '$-$$$$', 'key': 'price'}]}, 'headerLocation': 'Pelham Gardens', 'headerFullLocation': 'Pelham Gardens, Bronx', 'headerLocationGranularity': 'neighborhood', 'totalResults': 23, 'suggestedBounds': {'ne': {'lat': 40.86746562927998, 'lng': -73.83567284750141}, 'sw': {'lat': 40.85846562027997, 'lng': -73.84755104912306}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c9518076b35a143d5dc21dc', 'name': "Fratelli's", 'location': {'address': '2507 Eastchester Rd', 'lat': 40.86301897888721, 'lng': -73.84360740712835, 'labeledLatLngs': [{'label': 'display', 'lat': 40.86301897888721, 'lng': -73.84360740712835}], 'distance': 168, 'postal

...

{'meta': {'code': 200, 'requestId': '5d7ff558724750002c33f769'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': '$-$$$$', 'key': 'price'}, {'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Astoria', 'headerFullLocation': 'Astoria, Queens', 'headerLocationGranularity': 'neighborhood', 'totalResults': 23, 'suggestedBounds': {'ne': {'lat': 40.780423020142905, 'lng': -73.89635829141056}, 'sw': {'lat': 40.7714230111429, 'lng': -73.90822091642289}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4f68de6bd5fbee32e5f4f3a5', 'name': 'SingleCut Beersmiths', 'location': {'address': '19-33 37th St', 'crossStreet': 'btwn 19th & 20th Ave', 'lat': 40.778386547058325, 'lng': -73.9019024216154, 'labeledLatLngs': [{'label': 'display', 'lat': 40.778386547058325, 'lng': -73.90190242161

{'meta': {'code': 200, 'requestId': '5d7ff559a1979300383eb2d4'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': '$-$$$$', 'key': 'price'}, {'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Astoria', 'headerFullLocation': 'Astoria, Queens', 'headerLocationGranularity': 'neighborhood', 'totalResults': 23, 'suggestedBounds': {'ne': {'lat': 40.780423020142905, 'lng': -73.89635829141056}, 'sw': {'lat': 40.7714230111429, 'lng': -73.90822091642289}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4f68de6bd5fbee32e5f4f3a5', 'name': 'SingleCut Beersmiths', 'location': {'address': '19-33 37th St', 'crossStreet': 'btwn 19th & 20th Ave', 'lat': 40.778386547058325, 'lng': -73.9019024216154, 'labeledLatLngs': [{'label': 'display', 'lat': 40.778386547058325, 'lng': -73.90190242161

{'meta': {'code': 200, 'requestId': '5d7ff55992e7a9002c3840d1'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Current map view', 'headerFullLocation': 'Current map view', 'headerLocationGranularity': 'unknown', 'totalResults': 7, 'suggestedBounds': {'ne': {'lat': 40.63816931004365, 'lng': -74.12351561066195}, 'sw': {'lat': 40.629169301043646, 'lng': -74.13535292527818}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c446c9add1f2d7ff5ca7ff9', 'name': 'Enterprise Rent-A-Car', 'location': {'address': '1852 Richmond Ter', 'lat': 40.636863865318375, 'lng': -74.12707932669946, 'labeledLatLngs': [{'label': 'display', 'lat': 40.636863865318375, 'lng': -74.12707932669946}], 'distance': 407, 'postalCode': '10310', 'cc': 'US', 'city

{'meta': {'code': 200, 'requestId': '5d7ff55af9dbde0038d30755'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Current map view', 'headerFullLocation': 'Current map view', 'headerLocationGranularity': 'unknown', 'totalResults': 13, 'suggestedBounds': {'ne': {'lat': 40.52919938061813, 'lng': -74.21392204199819}, 'sw': {'lat': 40.520199371618126, 'lng': -74.22574009033735}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4bc65ec3b387d13adcd4c1e8', 'name': "Ralph's Ices", 'location': {'address': '6272 Amboy Rd', 'lat': 40.52396579948754, 'lng': -74.21501488824632, 'labeledLatLngs': [{'label': 'display', 'lat': 40.52396579948754, 'lng': -74.21501488824632}], 'distance': 415, 'postalCode': '10309', 'cc': 'US', 'city': 'Staten Isl

NameError: name 'Print' is not defined

In [71]:
car_rental_venues.head()

Borough Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   Bronx  Kingsbridge              40.881687              -73.902818   
1   Bronx  Kingsbridge              40.881687              -73.902818   
2   Bronx  Kingsbridge              40.881687              -73.902818   
3   Bronx  Kingsbridge              40.881687              -73.902818   
4   Bronx  Kingsbridge              40.881687              -73.902818   

                     Venue  Venue Latitude  Venue Longitude  \
0    Garden Gourmet Market       40.881350       -73.903389   
1             Leche y Miel       40.883709       -73.901606   
2  Kingsbridge Social Club       40.884545       -73.901964   
3               El Malecon       40.879338       -73.904457   
4              Sam's Pizza       40.879435       -73.905859   

              Venue Category  
0               Gourmet Shop  
1  Latin American Restaurant  
2                Pizza Place  
3       Caribbean Restaurant  
4                Pizza Place

In [72]:
car_rental_venues_onehot = pd.get_dummies(car_rental_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
car_rental_venues_onehot['Neighborhood'] = car_rental_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [car_rental_venues_onehot.columns[-1]] + list(car_rental_venues_onehot.columns[:-1])
car_rental_venues_onehot = car_rental_venues_onehot[fixed_columns]

car_rental_venues_onehot.head()

Neighborhood  Accessories Store  American Restaurant  Antique Shop  \
0  Kingsbridge                  0                    0             0   
1  Kingsbridge                  0                    0             0   
2  Kingsbridge                  0                    0             0   
3  Kingsbridge                  0                    0             0   
4  Kingsbridge                  0                    0             0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Arts & Crafts Store  \
0                 0                       0            0                    0   
1                 0                       0            0                    0   
2                 0                       0            0                    0   
3                 0                       0            0                    0   
4                 0                       0            0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Bagel Shop  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bakery  Bank  Bar  Beer Bar  Beer Store  Bike Rental / Bike Share  \
0       0     0    0         0           0                         0   
1       0     0    0         0           0                         0   
2       0     0    0         0           0                         0   
3       0     0    0         0           0                         0   
4       0     0    0         0           0                         0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Breakfast Spot  Brewery  \
0              0          0         0           0               0        0   
1              0          0         0           0               0        0   
2              0          0         0           0               0        0   
3              0          0         0           0               0        0   
4              0          0         0           0               0        0   

   Bubble Tea Shop  Buffet  Burger Joint  Burrito Place  Bus Station  \
0                0       0             0              0            0   
1                0       0             0              0            0   
2                0       0             0              0            0   
3                0       0             0              0            0   
4                0       0             0              0            0   

   Bus Stop  Café  Cajun / Creole Restaurant  Candy Store  \
0         0     0                          0            0   
1         0     0                          0            0   
2         0     0                          0            0   
3         0     0                          0            0   
4         0     0                          0            0   

   Cantonese Restaurant  Caribbean Restaurant  Cheese Shop  \
0                     0                     0            0   
1                     0                     0            0   
2                     0                     0            0   
3                     0                     1            0   
4                     0                     0            0   

   Chinese Restaurant  Clothing Store  Cocktail Bar  Coffee Shop  \
0                   0               0             0            0   
1                   0               0             0            0   
2                   0               0             0            0   
3                   0               0             0            0   
4                   0               0             0            0   

   Concert Hall  Convenience Store  Cosmetics Shop  Coworking Space  \
0             0                  0      

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category.

In [74]:
car_grouped = car_rental_venues_onehot.groupby('Neighborhood').mean().reset_index()
car_grouped.head()

Neighborhood  Accessories Store  American Restaurant  Antique Shop  \
0     Bath Beach                0.0             0.000000      0.000000   
1        Belmont                0.0             0.010000      0.000000   
2    Boerum Hill                0.0             0.011364      0.011364   
3   Clinton Hill                0.0             0.000000      0.000000   
4  College Point                0.0             0.000000      0.000000   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Arts & Crafts Store  \
0               0.0                     0.0     0.000000             0.000000   
1               0.0                     0.0     0.000000             0.000000   
2               0.0                     0.0     0.000000             0.022727   
3               0.0                     0.0     0.010753             0.021505   
4               0.0                     0.0     0.000000             0.000000   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Bagel Shop  \
0          0.021277            0.000000       0.000000        0.0    0.000000   
1          0.000000            0.000000       0.000000        0.0    0.000000   
2          0.000000            0.011364       0.000000        0.0    0.000000   
3          0.000000            0.000000       0.010753        0.0    0.021505   
4          0.069767            0.000000       0.000000        0.0    0.000000   

     Bakery      Bank       Bar  Beer Bar  Beer Store  \
0  0.021277  0.021277  0.000000       0.0         0.0   
1  0.050000  0.030000  0.020000       0.0         0.0   
2  0.022727  0.011364  0.034091       0.0         0.0   
3  0.010753  0.010753  0.010753       0.0         0.0   
4  0.046512  0.023256  0.046512       0.0         0.0   

   Bike Rental / Bike Share  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0                  0.021277            0.0   0.000000  0.000000    0.000000   
1                  0.000000            0.0   0.000000  0.000000    0.000000   
2                  0.000000            0.0   0.011364  0.011364    0.000000   
3                  0.021505            0.0   0.000000  0.010753    0.010753   
4                  0.000000            0.0   0.000000  0.000000    0.000000   

   Breakfast Spot  Brewery  Bubble Tea Shop    Buffet  Burger Joint  \
0             0.0      0.0         0.042553  0.000000      0.021277   
1             0.0      0.0         0.000000  0.000000      0.000000   
2             0.0      0.0         0.011364  0.000000      0.011364   
3             0.0      0.0         0.000000  0.000000      0.010753   
4             0.0      0.0         0.000000  0.023256      0.000000   

   Burrito Place  Bus Station  Bus Stop      Café  Cajun / Creole Restaurant  \
0       0.000000          0.0       0.0  0.000000                   0.000000   
1       0.000000          0.0       0.0  0.020000                   0.000000   
2       0.011364          0.0       0.0  0.000000                   0.011364   
3       0.000000          0.0       0.0  0.010753                   0.010753   
4       0.023256          0.0       0.0  0.023256                   0.000000   

   Candy Store  Cantonese Restaurant  Caribbean Restaurant  Cheese Shop  \
0          0.0              0.021277              0.000000         0.00   
1          0.0              0.000000              0.000000         0.01   
2          0.0              0.000000              0.011364         0.00   
3          0.0              0.000000              0.021505         0.00   
4          0.0              0.000000              0.023256         0.00   

   Chinese Restaurant  Clothing Store  Cocktail Bar  Coffee Shop  \
0            0.063830        0.021277      0.000000     0.021277   
1            0.000000        0.000000      0.000000     0.020000   
2            0.011364        0.000000      0.022727     0.045455   
3            0.021505        0.010753      0.021505     0.000000   
4            0.023256        0.000000      0.000000     0.000000   


# Let's print each neighborhood along with the top 5 most common venues.

In [75]:
num_top_venues = 5

for hood in car_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = car_grouped[car_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                venue  freq
0            Pharmacy  0.09
1  Chinese Restaurant  0.06
2         Pizza Place  0.04
3          Kids Store  0.04
4  Italian Restaurant  0.04


----Belmont----
                venue  freq
0  Italian Restaurant  0.18
1         Pizza Place  0.09
2       Deli / Bodega  0.08
3              Bakery  0.05
4                Bank  0.03


----Boerum Hill----
               venue  freq
0       Dance Studio  0.05
1        Coffee Shop  0.05
2                Bar  0.03
3                Spa  0.03
4  French Restaurant  0.03


----Clinton Hill----
                venue  freq
0  Italian Restaurant  0.05
1         Pizza Place  0.05
2  Mexican Restaurant  0.04
3   Indian Restaurant  0.03
4     Thai Restaurant  0.03


----College Point----
                       venue  freq
0                Pizza Place  0.09
1              Deli / Bodega  0.09
2           Asian Restaurant  0.07
3                        Bar  0.05
4  Latin American Restaurant  0.05


----East Elmhurs

The Neighborhoods **Steinway** and **East Elmhurst** are the ones which has **Rental Car Business** in the top 5 venues. Let's group all the neighborhoods and find the Neighborhood which is similar to Steinway and East Elmhurst. 

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [87]:
newyork_venues_onehot = pd.get_dummies(Master_df[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_venues_onehot['Neighborhood'] = Master_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_venues_onehot.columns[-1]] + list(newyork_venues_onehot.columns[:-1])
newyork_venues_onehot = newyork_venues_onehot[fixed_columns]

print("One hot encoding for Mastet dataframe is done..........................................................................")

new_york_grouped = newyork_venues_onehot.groupby('Neighborhood').mean().reset_index()

print("dataframe is grouped based on Neighborhood column and mean function is applied to all columns..........................")







One hot encoding for Mastet dataframe is done..........................................................................
dataframe is grouped based on Neighborhood column and mean function is applied to all columns..........................


In [88]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [89]:
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = new_york_grouped['Neighborhood']

for ind in np.arange(new_york_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(new_york_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place           Supermarket   
1       Annadale           Pizza Place                Bakery   
2  Arden Heights              Pharmacy           Coffee Shop   
3      Arlington              Bus Stop          Intersection   
4       Arrochar              Bus Stop         Deli / Bodega   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0    Chinese Restaurant              Pharmacy      Department Store  
1            Bagel Shop         Train Station            Sports Bar  
2              Bus Stop           Pizza Place   Filipino Restaurant  
3  Caribbean Restaurant         Women's Store           Fish Market  
4    Italian Restaurant           Pizza Place                 Hotel

In [90]:
neighborhoods_venues_sorted.shape[0]

300

# Cluster Neighborhoods.

In [91]:
# set number of clusters
kclusters = 5

new_york_grouped_clustering = new_york_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(new_york_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 4, 2, 0, 0, 0, 0, 0])

In [92]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

newyork_merged = Master_df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
newyork_merged = newyork_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

newyork_merged.head() # check the last columns!

Borough Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   Bronx    Wakefield              40.894705              -73.847201   
1   Bronx    Wakefield              40.894705              -73.847201   
2   Bronx    Wakefield              40.894705              -73.847201   
3   Bronx    Wakefield              40.894705              -73.847201   
4   Bronx    Wakefield              40.894705              -73.847201   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato       40.894123       -73.845892   
1                                 Rite Aid       40.896649       -73.844846   
2                         Carvel Ice Cream       40.890487       -73.848568   
3  Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
4                                    Shell       40.894187       -73.845862   

         Venue Category  Cluster Labels 1st Most Common Venue  \
0          Dessert Shop               4           Gas Station   
1              Pharmacy               4           Gas Station   
2        Ice Cream Shop               4           Gas Station   
3  Caribbean Restaurant               4           Gas Station   
4           Gas Station               4           Gas Station   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0          Dessert Shop        Sandwich Place  Caribbean Restaurant   
1          Dessert Shop        Sandwich Place  Caribbean Restaurant   
2          Dessert Shop        Sandwich Place  Caribbean Restaurant   
3          Dessert Shop        Sandwich Place  Caribbean Restaurant   
4          Dessert Shop        Sandwich Place  Caribbean Restaurant   

  5th Most Common Venue  
0        Ice Cream Shop  
1        Ice Cream Shop  
2        Ice Cream Shop  
3        Ice Cream Shop  
4        Ice Cream Shop

# Let's Visualize the clusters.

Let's find out which cluster Steinway and East Elmhurst belong to.

In [99]:
Steinway_label = newyork_merged[newyork_merged['Neighborhood'] == 'Steinway']['Cluster Labels'].iloc[0]
East_Elmhurst_label = newyork_merged[newyork_merged['Neighborhood'] == 'East Elmhurst']['Cluster Labels'].iloc[0]

print('The Neighbourhood {} belong to cluster {}'.format("Steinway",Steinway_label))
print('The Neighbourhood {} belong to cluster {}'.format("East Elmhurst",East_Elmhurst_label))

The Neighbourhood Steinway belong to cluster 0
The Neighbourhood East Elmhurst belong to cluster 0


Let's take a look at those Neighborhoods which fall into Cluster 0.

In [104]:
cluster_zero = newyork_merged[newyork_merged['Cluster Labels'] == 0]

In [133]:
cluster_table = pd.pivot_table(cluster_zero, index = ['Neighborhood'])
cluster_table.head()

Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                   
Allerton                    0              40.865788              -73.859319   
Annadale                    0              40.538114              -74.178549   
Arden Heights               0              40.549286              -74.185887   
Arverne                     0              40.589144              -73.791992   
Astoria                     0              40.768509              -73.915654   

               Venue Latitude  Venue Longitude  
Neighborhood                                    
Allerton            40.865057       -73.859414  
Annadale            40.541011       -74.177195  
Arden Heights       40.551278       -74.185412  
Arverne             40.590142       -73.795322  
Astoria             40.766627       -73.916589

In [137]:
cluster_table['Neighborhood'] = cluster_table.index

In [140]:
cluster_table.columns

Index(['Cluster Labels', 'Neighborhood Latitude', 'Neighborhood Longitude',
       'Venue Latitude', 'Venue Longitude', 'Neighborhood'],
      dtype='object')

In [146]:
# create map

map_clusters = folium.Map(location=[40.7127281, -74.0060152], zoom_start=15)


# add markers to the map
for index,row in cluster_table.iterrows():
    label = folium.Popup(row['Neighborhood'] + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [row["Neighborhood Latitude"], row["Neighborhood Longitude"]],
        radius=2,
        popup=label,
        fill_opacity=0.7).add_to(map_clusters)
    
       
       


    
newyorkArr = cluster_table[['Neighborhood Latitude', 'Neighborhood Longitude']].as_matrix()

# plot heatmap
map_clusters.add_children(plugins.HeatMap(newyorkArr, radius=15))
    
map_clusters


C:\Users\Welcome\Anaconda3\lib\site-packages\ipykernel_launcher.py:20: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
C:\Users\Welcome\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: FutureWarning: Method `add_children` is deprecated. Please use `add_child` instead.


***Conclusion:
    The Neighborhoods that are suggested are as shown in the above heat map. The Businesses can be started in any of the above locations.***